## Proprocessing ##

df = pd.read_csv("../data/publication.csv", usecols=['abstract', 'keywords','language'],encoding='utf8')
#only use the entry that have an abstarct and keywords

scraping_publications = df[df['keywords'].notna() & df['abstract'].notna()]     # Dataframe in Panda

In [31]:
import pandas as pd
import numpy as np
import re
import ast
import html
#import utils

# Einlesen des Dataframes
df = pd.read_csv("unbereinigteDB_Test_full.csv", encoding='utf8',sep=';')
#df = utils.get_collection_df_from_mongo("publication_filled")

#alte Datenbankdatei erstellen
#df.to_csv("Datanbankcsv.csv", sep=';', encoding='utf-8', index=False)
df

_id        id  \
0     63b9ec46ccabac595f0dda68  10101316   
1     63b9ec46ccabac595f0dda69  10105507   
2     63b9ec46ccabac595f0dda6a  10971967   
3     63b9ec46ccabac595f0dda6b  10976734   
4     63b9ec46ccabac595f0dda6c  10982470   
...                        ...       ...   
3922  63ba13a3cd376a2aacf5ce22   9716991   
3923  63ba13a3cd376a2aacf5ce23   9718109   
3924  63ba13a3cd376a2aacf5ce24   9725364   
3925  63ba13a3cd376a2aacf5ce25   9728223   
3926  63ba13a3cd376a2aacf5ce26   9728299   

                                                cfTitle  \
0     Configuring Reference Models - An Integrated A...   
1     Konnektionistische Tourenplanung für die dezen...   
2     Cryptocoin-Schulden – Haftung und Risikovertei...   
3     Benefits and Perils of Virtual Modes of Organi...   
4     Dynamic Decision Making in Energy Systems with...   
...                                                 ...   
3922  Informationsmanagement I: Eine managementorien...   
3923  Über das Zusammenwirken der Gestaltung und Eme...   
3924  Simulation model concept for evaluating spare ...   
3925  Dienstleistungsinnovationen für Elektromobilit...   
3926  Towards a Common Reference Architecture for th...   

                                                  cfUri  \
0                                                   NaN   
1                                                   NaN   
2                                                   NaN   
3                                                   NaN   
4                                                   NaN   
...                                                 ...   
3922                                                NaN   
3923                                                NaN   
3924                                                NaN   
3925  http://www.elektromobilitaet-dienstleistungen....   
3926                                                NaN   

                                               keywords  \
0                                                   NaN   
1                                                   NaN   
2                                                   NaN   
3                                                   NaN   
4                                                   NaN   
...                                                 ...   
3922                                                NaN   
3923  Geschäftsprozessmanagement; Organisationsrouti...   
3924                                                NaN   
3925  Dienstleistungsforschung; Service Science; Ele...   
3926                                                NaN   

                            doi  \
0                           NaN   
1                           NaN   
2                           NaN   
3                           NaN   
4                           NaN   
...                         ...   
3922                        NaN   
3923  10.1007/s11576-014-0425-3   
3924                        NaN   
3925                        NaN   
3926                        NaN   

                                             srcAuthors  \
0                     Knackstedt R, Janiesch C, Rieke T   
1                                 Pietsch W, Teubner RA   
2                                                 Pesch   
3                     Schellhammer Stefan, Klein Stefan   
4                                    Meisel S, Powell W   
...                                                 ...   
3922                                Teubner RA, Klein S   
3923                                 Beverungen, Daniel   
3924  Frazzon Enzo, Albrecht André, Israel Eduardo, ...   
3925                                                NaN   
3926  Böhle, C., Hellingrath, B., Cordes, A., Höhenb...   

                                                authors  \
0                                                   NaN   
1                                                   NaN   
2                                                   NaN   
3    

examine Dateframe structure, anomalies of dois, keywords, titles and abstracts

In [125]:
import math
import re

# how is the Doi structured
# 10.XXXX/abc

def clean_dois(df_dois):
    """
    This function extracts all the doi by searching for the doi pattern 10.XXXX/abc
    :df_dois: input column of the dataframe "doi"
    :return: list of dois
    """
    dois = []
    for text in df_dois:
        if type(text) == str:
            match = re.search(r'10\.[0-9]+\/[a-zA-Z0-9\.\-\_]+', text)
            if match:
                dois.append(match.group())
            else:
                dois.append(None)
        else:
            dois.append(None)
    return dois

def getDoi2(dfDoi):
    return [text for text in dfDoi if type(text) is str and not(re.match(r'10\.[0-9]+\/[a-zA-Z0-9\.\-\_]+', text)) ]



liste = clean_dois(df["doi"])
liste2 = getDoi2(df["doi"])
#print(liste)
print(liste2,"doiwithoutdoimatch")

getTypes(liste)
len(liste)


['10.1.1.93.7074', 'https://doi.org/10.1016/j.procs.2015.08.335', 'https://aclanthology.org/2022.lrec-1.585', 'https://doi.org/10.1007/978-3-031-05544-7_6', 'https://doi.org/10.1137/1.9781611977172.32', 'https://doi.org/10.1002/anie.202204647', 'https://doi.org/10.48550/arXiv.2207.04003', 'https://doi.org/10.1007/978-3-031-19682-9_35', 'https://doi.org/10.1007/978-3-031-08754-7_63'] doiwithoutdoimatch


3927

In [84]:
# Group by different types in the columns
def getTypes(column):
    liste = []
    for row in column:
        if type(row) not in liste:
            liste.append(type(row))
    return liste
print(getTypes(df["cfTitle"]), "title")
print(getTypes(df["cfAbstr"]), "abstr")
print(getTypes(df["keywords"]),"keywords")
print(getTypes(df["doi"]),"doi")

[<class 'str'>] title
[<class 'float'>, <class 'str'>] abstr
[<class 'float'>, <class 'str'>] keywords
[<class 'float'>, <class 'str'>] doi


In [ ]:
# detect specific Types in List
def getTypeInCol(column):
    liste = []
    for row in column:
        if type(row) is not list:
            liste.append(type(row))
    return liste

print(getTypeInCol(df["doi"]),"keywords")

In [139]:
keyses = df["cfAbstr"]

url_pattern = re.compile(r'http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+')

# loop through the list and extract URLs from strings only
extracted_urls = []
for item in keyses:
    extracted_url = re.findall(url_pattern, str(item))
    if extracted_url:
        extracted_urls.append(extracted_url[0])

print(extracted_urls)


['http://cswww.essex.ac.uk/technical-reports/2001/CSM-349.pdf,', 'https://de.wikipedia.org/wiki/Big_Data,', 'http://rstudio.org)', 'http://cran.r-project.org/web/packages/SPOT/index.html', 'http://cran.r-project.org/.', 'http://www.astro.rub.de/polsterer/quasar-candidates.csv.', 'https://github.com/COINtoolbox/DRACULA).', 'https://github.com/COINtoolbox/DRACULA).', 'https://github.com/gieseke/bufferkdtree', 'https://cointoolbox.github.io/GMM_Catalogue/.', 'https://www.driver-project.eu/', 'https://en.unesco.org/themes/building-knowledge-societies/oer/recommendation', 'https://mfga.uni-muenster.de.']


In [141]:
keyses[14]

'<p>Die im Maschinen- und Anlagenbau zunehmend verbreitete Erstellung\r\nhybrider Leistungsbündel aus Sachgütern und Dienstleistungen wird häufig in\r\nNetzwerken aus Kunden und Lieferanten entlang der Wertschöpfungskette ausgeführt. Je nach Ausrichtung des Geschäftsmodells und der Rollenverteilung innerhalb des Netzwerks ändern sich die Prozesse der beteiligten Wertschöpfungspartner. Der vorliegende Beitrag analysiert die sich hieraus ergebenden Anforderungen\r\nan Prozessmodelle für die hybride Wertschöpfung aus der Perspektive zweier\r\nWertschöpfungsnetzwerke im Maschinen- und Anlagenbau. Als ein Lösungsansatz\r\nwerden konfigurierbare Prozessmodelle identifiziert. Für den unternehmensübergreifenden Prozess der Störfallbeseitigung wurde ein Prozessmodell konstruiert,\r\ndas als Ausgangslösung toolgestützt an die Erfordernisse speziell ausgeprägter\r\nNetzwerke angepasst werden kann.\xa0<br /></p>'

In [ ]:
# Teste ob HTML-Tags in abstract drin sind noch drin sind:
def getAbstractList(df_Abstract):
    rows_with_html = []
    for row in df_Abstract:
        if row is not None and any(x in [">","<"] for x in str(row)):
            rows_with_html.append(row)
    return rows_with_html

print(getAbstractList(cleanTextList(df["cfAbstr"]))) # Nur Abstracts die < > beinhalten, manuelle Überprüfung

# Teste ob HTML-Tags in Titeln noch drin sind:
def getTitleList(df_Title):
    rows_with_html = []
    for row in df_Title:
        if row is not None and any(x in [">","<"] for x in str(row)):
            rows_with_html.append(row)
    return rows_with_html

print(getTitleList(cleanTextList(df["cfTitle"])))

# Teste ob Längen noch passen
keys = cleanKeywordsList(df["keywords"])
absts = cleanTextList(df["cfAbstr"])
title = cleanTextList(df["cfTitle"])

print(len(keys),len(absts),len(title))


Investigate what kind of "noise" is generally included

In [13]:
# Untersuche, welche Art von Keywörter es gibt, die keine Liste, ";" , "," sind
def differentKeywords(df_keywords):
    cleaned_list = []
    reg_list = re.compile("\[.*?\]")
    for row in df_keywords:
        if type(row) is str:
            if not(reg_list.match(str(row)) or ";" in row or "," in row):
                cleaned_list.append(row)
    return cleaned_list

ls = differentKeywords(df["keywords"])
print(ls)


['2', 'waml', 'wasl', 'cim mda mdsd pim psm wasl', 'Market theory', 'fischer14underlay', 'Consumer Search Behaviour', 'Supply Chain Flexibility', 'Photo Forensics', 'Humanitarian Logistics', 'AgeGov', 'Humanitarian Logistics', 'entity-relationship diagram', 'functional logic programming', 'humanitarian logistics', 'Configuration Errors', 'Creativity', 'Elektromobilität', '-', 'Password Strength', '-', '-', 'Digital technologies', 'Analytics as a Service', '-', '-', '-', 'Swarm Intelligence']


In [142]:
# Reguläre Ausdrücke; Out: Text sonst None
def remove_html_tags(text):
    # remove HTML tags
    clean = re.compile('<.*?>')
    result = re.sub(clean, '', text)
    # remove \r and \n characters
    result = result.replace("\r", "").replace("\n", "")
    # check if the result exists and has a length greater than 1
    if result and len(result) > 1:
        return result
    #else return None

# BereinigeText in eine Liste auf HMTL, NoneType, "-", HTML Encode
def cleanTextList(df_Abstract):
    rows_without_html = []
    for row in df_Abstract:
        if type(row) is not str:
            rows_without_html.append(None)
        else:
            result = remove_html_tags(str(row))
            if result is not None:
                result = html.unescape(result)
            rows_without_html.append(result)
    return rows_without_html

#BereinigeKeywörter Liste erkennen, separator: ";", "," , NoneType, "-", HTML Encode
def cleanKeywordsList(df_keywords):
    cleaned_list = []
    reg_list = re.compile("\[.*?\]")

    for row in df_keywords:
        if row is None or type(row) is float or len(row) <= 1:
            cleaned_list.append(None)
        else:    
            if type(row) is list or reg_list.match(str(row)):
                result = ast.literal_eval(str(row))
            else:
                if ";" in row:
                    result = [x.strip() for x in row.split(';')]
                else:
                    result = [x.strip() for x in row.split(',')]
            result = [x.lower() for x in result]
            cleaned_list.append(html.unescape(result))
    return cleaned_list

keywordlist = cleanKeywordsList(df["keywords"])
print(keywordlist[:15])
print(df["keywords"][:15])

[None, None, None, None, None, None, None, None, None, None, None, None, None, None, ['wertschöpfung', 'hybrid', 'prozessmodell', 'netzwerke']]
0                                                 NaN
1                                                 NaN
2                                                 NaN
3                                                 NaN
4                                                 NaN
5                                                 NaN
6                                                 NaN
7                                                 NaN
8                                                 NaN
9                                                 NaN
10                                                NaN
11                                                NaN
12                                                NaN
13                                                NaN
14    Wertschöpfung; Hybrid; Prozessmodell; Netzwerke
Name: keywords, dtype: object


In [143]:
def makeNewDataframe(dataframe):
   
    df_new = dataframe.copy()
    title = cleanTextList(dataframe["cfTitle"])
    absts = cleanTextList(dataframe["cfAbstr"])
    keys = cleanKeywordsList(dataframe["keywords"])
    dois = clean_dois(dataframe["doi"])
    
    df_new["doi"] = dois
    df_new["cfTitle"] = title
    df_new["cfAbstr"] = absts
    df_new["keywords"] = keys
    #df_new["result_flag"] = test(dataframe["result_flag"])

    return df_new

new_df = makeNewDataframe(df)
new_df.to_csv("bereinigteDB.csv", sep=';', encoding='utf-8', index=False)
new_df

_id        id  \
0     63b9ec46ccabac595f0dda68  10101316   
1     63b9ec46ccabac595f0dda69  10105507   
2     63b9ec46ccabac595f0dda6a  10971967   
3     63b9ec46ccabac595f0dda6b  10976734   
4     63b9ec46ccabac595f0dda6c  10982470   
5     63b9ec46ccabac595f0dda6d  11916895   
6     63b9ec46ccabac595f0dda6e  11917046   
7     63b9ec46ccabac595f0dda6f  11925120   
8     63b9ec46ccabac595f0dda70  12236895   
9     63b9ec46ccabac595f0dda71  12236971   
10    63ba13a3cd376a2aacf5beda  12237056   
11    63ba13a3cd376a2aacf5bedb  12237142   
12    63ba13a3cd376a2aacf5bedc  12237222   
13    63ba13a3cd376a2aacf5bedd  12237300   
14    63ba13a3cd376a2aacf5bede  12237378   
15    63ba13a3cd376a2aacf5bedf  12237457   
16    63ba13a3cd376a2aacf5bee0  12237601   
17    63ba13a3cd376a2aacf5bee1  12237679   
18    63ba13a3cd376a2aacf5bee2  12237767   
19    63ba13a3cd376a2aacf5bee3  12237848   
20    63ba13a3cd376a2aacf5bee4  12237937   
21    63ba13a3cd376a2aacf5bee5  12238021   
22    63ba13a3cd376a2aacf5bee6  12238097   
23    63ba13a3cd376a2aacf5bee7  12238172   
24    63ba13a3cd376a2aacf5bee8  12238256   
25    63ba13a3cd376a2aacf5bee9  12238332   
26    63ba13a3cd376a2aacf5beea  12238419   
27    63ba13a3cd376a2aacf5beeb  12238508   
28    63ba13a3cd376a2aacf5beec  12238593   
29    63ba13a3cd376a2aacf5beed  12238675   
30    63ba13a3cd376a2aacf5beee  12238763   
31    63ba13a3cd376a2aacf5beef  12238839   
32    63ba13a3cd376a2aacf5bef0  12238916   
33    63ba13a3cd376a2aacf5bef1  12238999   
34    63ba13a3cd376a2aacf5bef2  12239075   
35    63ba13a3cd376a2aacf5bef3  12239159   
36    63ba13a3cd376a2aacf5bef4  12239249   
37    63ba13a3cd376a2aacf5bef5  12239334   
38    63ba13a3cd376a2aacf5bef6  12239414   
39    63ba13a3cd376a2aacf5bef7  12239500   
40    63ba13a3cd376a2aacf5bef8  12239581   
41    63ba13a3cd376a2aacf5bef9  12239667   
42    63ba13a3cd376a2aacf5befa  12239743   
43    63ba13a3cd376a2aacf5befb  12239817   
44    63ba13a3cd376a2aacf5befc  12239897   
45    63ba13a3cd376a2aacf5befd  12239976   
46    63ba13a3cd376a2aacf5befe  12240052   
47    63ba13a3cd376a2aacf5beff  12240134   
48    63ba13a3cd376a2aacf5bf00  12240210   
49    63ba13a3cd376a2aacf5bf01  12240298   
50    63ba13a3cd376a2aacf5bf02  12240372   
51    63ba13a3cd376a2aacf5bf03  12240450   
52    63ba13a3cd376a2aacf5bf04  12240525   
53    63ba13a3cd376a2aacf5bf05  12240602   
54    63ba13a3cd376a2aacf5bf06  12240680   
55    63ba13a3cd376a2aacf5bf07  12240758   
56    63ba13a3cd376a2aacf5bf08  12240832   
57    63ba13a3cd376a2aacf5bf09  12240909   
58    63ba13a3cd376a2aacf5bf0a  12240986   
59    63ba13a3cd376a2aacf5bf0b  12241061   
60    63ba13a3cd376a2aacf5bf0c  12241137   
61    63ba13a3cd376a2aacf5bf0d  12241215   
62    63ba13a3cd376a2aacf5bf0e  12241289   
63    63ba13a3cd376a2aacf5bf0f  12241366   
64    63ba13a3cd376a2aacf5bf10  12241447   
65    63ba13a3cd376a2aacf5bf11  12241536   
66    63ba13a3cd376a2aacf5bf12  12241614   
67    63ba13a3cd376a2aacf5bf13  12241689   
68    63ba13a3cd376a2aacf5bf14  12241767   
69    63ba13a3cd376a2aacf5bf15  12241847   
70    63ba13a3cd376a2aacf5bf16  12241923   
71    63ba13a3cd376a2aacf5bf17  12241998   
72    63ba13a3cd376a2aacf5bf18  12242078   
73    63ba13a3cd376a2aacf5bf19  12242158   
74    63ba13a3cd376a2aacf5bf1a  12242237   
75    63ba13a3cd376a2aacf5bf1b  12242315   
76    63ba13a3cd376a2aacf5bf1c  12242393   
77    63ba13a3cd376a2aacf5bf1d  12242467   
78    63ba13a3cd376a2aacf5bf1e  12242543   
79    63ba13a3cd376a2aacf5bf1f  12242625   
80    63ba13a3cd376a2aacf5bf20  12242700   
81    63ba13a3cd376a2aacf5bf21  12242774   
82    63ba13a3cd376a2aacf5bf22  12242848   
83    63ba13a3cd376a2aacf5bf23  12242922   
84    63ba13a3cd376a2aacf5bf24  12242996   
85    63ba13a3cd376a2aacf5bf25  12243070   
86    63ba13a3cd376a2aacf5bf26  12243145   
87    63ba13a3cd376a2aacf5bf27  12243225   
88    63ba13a3cd376a2aacf5bf28  12243304   
89    63ba13a3cd376a2aacf5bf29  12243382   
90    63ba13a3cd376a2aa

In [89]:
print(getTypes(new_df["keywords"]))
print(getTypes(new_df["cfTitle"]))
print(getTypes(new_df["cfAbstr"]))


[<class 'NoneType'>, <class 'list'>]
[<class 'str'>]
[<class 'NoneType'>, <class 'str'>]


In [ ]:
def preprocessing(df):
 
    #df = utils.get_collection_df_from_mongo(table)
    #df = pd.read_csv("ps-research-map\Preprocessing\publications_eng.csv", encoding='utf8')
    new_df = makeNewDataframe(df)
    return new_df

In [42]:
new_df

_id        id  \
0     63b9ec46ccabac595f0dda68  10101316   
1     63b9ec46ccabac595f0dda69  10105507   
2     63b9ec46ccabac595f0dda6a  10971967   
3     63b9ec46ccabac595f0dda6b  10976734   
4     63b9ec46ccabac595f0dda6c  10982470   
...                        ...       ...   
3922  63ba13a3cd376a2aacf5ce22   9716991   
3923  63ba13a3cd376a2aacf5ce23   9718109   
3924  63ba13a3cd376a2aacf5ce24   9725364   
3925  63ba13a3cd376a2aacf5ce25   9728223   
3926  63ba13a3cd376a2aacf5ce26   9728299   

                                                cfTitle  \
0     Configuring Reference Models - An Integrated A...   
1     Konnektionistische Tourenplanung für die dezen...   
2     Cryptocoin-Schulden – Haftung und Risikovertei...   
3     Benefits and Perils of Virtual Modes of Organi...   
4     Dynamic Decision Making in Energy Systems with...   
...                                                 ...   
3922  Informationsmanagement I: Eine managementorien...   
3923  Über das Zusammenwirken der Gestaltung und Eme...   
3924  Simulation model concept for evaluating spare ...   
3925  Dienstleistungsinnovationen für Elektromobilit...   
3926  Towards a Common Reference Architecture for th...   

                                                  cfUri  \
0                                                   NaN   
1                                                   NaN   
2                                                   NaN   
3                                                   NaN   
4                                                   NaN   
...                                                 ...   
3922                                                NaN   
3923                                                NaN   
3924                                                NaN   
3925  http://www.elektromobilitaet-dienstleistungen....   
3926                                                NaN   

                                               keywords  \
0                                                  None   
1                                                  None   
2                                                  None   
3                                                  None   
4                                                  None   
...                                                 ...   
3922                                               None   
3923  [Geschäftsprozessmanagement, Organisationsrout...   
3924                                               None   
3925  [Dienstleistungsforschung, Service Science, El...   
3926                                               None   

                            doi  \
0                           NaN   
1                           NaN   
2                           NaN   
3                           NaN   
4                           NaN   
...                         ...   
3922                        NaN   
3923  10.1007/s11576-014-0425-3   
3924                        NaN   
3925                        NaN   
3926                       None   

                                             srcAuthors  \
0                     Knackstedt R, Janiesch C, Rieke T   
1                                 Pietsch W, Teubner RA   
2                                                 Pesch   
3                     Schellhammer Stefan, Klein Stefan   
4                                    Meisel S, Powell W   
...                                                 ...   
3922                                Teubner RA, Klein S   
3923                                 Beverungen, Daniel   
3924  Frazzon Enzo, Albrecht André, Israel Eduardo, ...   
3925                                               None   
3926  Böhle, C., Hellingrath, B., Cordes, A., Höhenb...   

                                                authors  \
0                                                  None   
1                                                  None   
2                                                  None   
3    

In [43]:
df

_id        id  \
0     63b9ec46ccabac595f0dda68  10101316   
1     63b9ec46ccabac595f0dda69  10105507   
2     63b9ec46ccabac595f0dda6a  10971967   
3     63b9ec46ccabac595f0dda6b  10976734   
4     63b9ec46ccabac595f0dda6c  10982470   
...                        ...       ...   
3922  63ba13a3cd376a2aacf5ce22   9716991   
3923  63ba13a3cd376a2aacf5ce23   9718109   
3924  63ba13a3cd376a2aacf5ce24   9725364   
3925  63ba13a3cd376a2aacf5ce25   9728223   
3926  63ba13a3cd376a2aacf5ce26   9728299   

                                                cfTitle  \
0     Configuring Reference Models - An Integrated A...   
1     Konnektionistische Tourenplanung für die dezen...   
2     Cryptocoin-Schulden – Haftung und Risikovertei...   
3     Benefits and Perils of Virtual Modes of Organi...   
4     Dynamic Decision Making in Energy Systems with...   
...                                                 ...   
3922  Informationsmanagement I: Eine managementorien...   
3923  Über das Zusammenwirken der Gestaltung und Eme...   
3924  Simulation model concept for evaluating spare ...   
3925  Dienstleistungsinnovationen für Elektromobilit...   
3926  Towards a Common Reference Architecture for th...   

                                                  cfUri  \
0                                                   NaN   
1                                                   NaN   
2                                                   NaN   
3                                                   NaN   
4                                                   NaN   
...                                                 ...   
3922                                                NaN   
3923                                                NaN   
3924                                                NaN   
3925  http://www.elektromobilitaet-dienstleistungen....   
3926                                                NaN   

                                               keywords  \
0                                                  None   
1                                                  None   
2                                                  None   
3                                                  None   
4                                                  None   
...                                                 ...   
3922                                                NaN   
3923  Geschäftsprozessmanagement; Organisationsrouti...   
3924                                                NaN   
3925  Dienstleistungsforschung; Service Science; Ele...   
3926                                               None   

                            doi  \
0                           NaN   
1                           NaN   
2                           NaN   
3                           NaN   
4                           NaN   
...                         ...   
3922                        NaN   
3923  10.1007/s11576-014-0425-3   
3924                        NaN   
3925                        NaN   
3926                       None   

                                             srcAuthors  \
0                     Knackstedt R, Janiesch C, Rieke T   
1                                 Pietsch W, Teubner RA   
2                                                 Pesch   
3                     Schellhammer Stefan, Klein Stefan   
4                                    Meisel S, Powell W   
...                                                 ...   
3922                                Teubner RA, Klein S   
3923                                 Beverungen, Daniel   
3924  Frazzon Enzo, Albrecht André, Israel Eduardo, ...   
3925                                               None   
3926  Böhle, C., Hellingrath, B., Cordes, A., Höhenb...   

                                                authors  \
0                                                  None   
1                                                  None   
2                                                  None   
3    